In [1]:
#You don't need to change anything in this block, although the modules need to be installed to run this notebook

#We import numpy to handle vectors and some math
import numpy as np

#We import pandas to create a data frame of the experiment data
#Such a table can later be used for plotting our results
import pandas as pd

#We import bokeh to create a small application that plots our stored results
from bokeh.themes import Theme
from bokeh.io import show, output_notebook, curdoc
from bokeh.plotting import figure
from bokeh.transform import linear_cmap, factor_cmap
from bokeh.palettes import Spectral6
from bokeh.models import ColumnDataSource, Slider, Column, Toggle
from bokeh.server import callbacks

In [2]:
#You don't need to change anything in this block

def get_initial_followers_state():
    '''Generates the state of follower particles for t0'''
    followers_positions = 2 * (np.random.rand(num_followers, 2) - 0.5)
    followers_velocities = np.zeros((num_followers, 2))
    return followers_positions, followers_velocities

def get_leader_position(t):
    '''Generates the position of the leader based on input time'''
    step_size = leader_speed
    distance_covered = step_size * t
    
    circle_radius = 1
    circle_circumference = 2 * circle_radius * np.pi
    percent_circle_completed = distance_covered / circle_circumference
    radians = percent_circle_completed * 2 * np.pi
    
    leader_x = np.sin(radians)
    leader_y = np.cos(radians)
    return np.array([leader_x, leader_y])

def magnitude(vector):
    '''Returns the magnitude of a vector'''
    return np.linalg.norm(vector)

def distance_between(position, goal):
    '''Returns the distance between two points'''
    return magnitude(goal - position)

def vector_towards(position, goal):
    '''Returns the vector that points from the position to the goal'''
    return goal - position

def direction_towards(position, goal):
    '''Returns a vector pointing from the position towards the goal with magnitude 1'''
    return (goal - position) / magnitude(goal - position)

def to_dataframe(t, followers_positions, leader_position):
    '''Converts the particle state at one timestep to a dataframe'''
    df = pd.DataFrame()
    df['t'] = np.repeat(t, num_followers + 1)
    df['type'] = np.append(np.repeat('Follower', num_followers), 'Leader')
    df['x'] = np.append(followers_positions[:, 0], leader_position[0])
    df['y'] = np.append(followers_positions[:, 1], leader_position[1])
    return df

In [3]:
#Here we define the possible force functions (attraction / repulsion)
#You can play around with the parameters of the functions or create your own functions
 
def force_random(followers_positions, leader_position, d=0.7, k_followers=0.01, k_leader=0.5): 
    '''Force function with linear attraction and distance proportional, random offset'''
    force = np.zeros((num_followers, 2))
    
    for i in range(num_followers):
        vector_to_leader = vector_towards(followers_positions[i], leader_position)
        force[i] += k_leader * (d - np.random.rand(2)) * vector_to_leader
        
        for j in range(num_followers):
            if i == j:
                continue
            vector_to_follower_j = vector_towards(followers_positions[i], followers_positions[j])
            force[i] += k_followers * (d - np.random.rand(2)) * vector_to_follower_j
    return force

def force_simple_comfortable_distance(followers_positions, leader_position, d=0.5, k_followers=0.1, k_leader=0.5): 
    '''Force function to keep a comfortable distance with linear attraction and repulsion'''
    force = np.zeros((num_followers, 2))
    
    for i in range(num_followers):
        distance_to_leader = distance_between(followers_positions[i], leader_position)
        direction_to_leader = direction_towards(followers_positions[i], leader_position)
        leader_force = k_leader * (distance_to_leader - d) * direction_to_leader
        
        cohesion_force = 0
        for j in range(num_followers):
            if i == j:
                continue
            distance_to_follower_j = distance_between(followers_positions[i], followers_positions[j])
            direction_to_follower_j = direction_towards(followers_positions[i], followers_positions[j])
            cohesion_force += k_followers * (distance_to_follower_j - d) * direction_to_follower_j
            
        force[i] = leader_force + cohesion_force
    return force

In [4]:
#You don't need to change anything in this block

def update(followers_positions, followers_velocities, leader_position):
    '''Calculates new positions and velocities based on the state given as input'''
    new_velocities = inertia * followers_velocities + force_function(followers_positions, leader_position)
    new_positions = followers_positions + new_velocities
    return new_positions, new_velocities

def run():
    '''Iterates over all time steps, updates the particle states, and writes each state to a dataframe'''
    data = []
    leader_position = get_leader_position(0)
    followers_positions, followers_velocities = get_initial_followers_state()
    data.append(to_dataframe(0, followers_positions, leader_position))
    
    for t in range(1, num_time_steps, 1):
        leader_position = get_leader_position(t)
        followers_positions, followers_velocities = update(followers_positions, followers_velocities, leader_position)
        data.append(to_dataframe(t, followers_positions, leader_position))
        
    return pd.concat(data)

In [5]:
#You don't need to change anything in this block

def bokeh_app(doc):
    '''Defining a small application to plot dataframes generated from the run function'''
    def callback_update():
        if toggle.active:
            slider.value += 1
            if slider.value > num_time_steps:
                slider.value = 0
        source.data = ColumnDataSource.from_df(df.loc[df.t.eq(slider.value)])
            
    toggle = Toggle(label="Play/Stop")
    slider = Slider(start=0, end=num_time_steps-1, title="t", value=0)
    
    source = ColumnDataSource(df.loc[df.t.eq(0)])  
    plot = figure(x_range=(-2.0,2.0), y_range=(-2.0,2.0))
    plot.circle(size=20, radius=0.05, alpha=0.75, source=source, x='x', y='y', color=factor_cmap('type', Spectral6, ['Follower', 'Leader']))
    
    layout = Column(slider, toggle, plot)
    
    doc.add_root(layout)
    doc.add_periodic_callback(callback_update, 50)
    doc.theme = Theme(json= {
        "attrs" : 
        {
            "Figure" : 
            {
                "background_fill_color" : "#FAFAFA",
                "outline_line_color" : "white",
                "toolbar_location" : "above",
                "height" : 500,
                "width" : 500
            },
            "Grid" : 
            {
                "grid_line_dash" : [6, 4],
                "grid_line_color" : "white"
            }
        }
    })

In [6]:
#Here we define some global parameters used in the above functions
#You can change these and observe how the behavior changes

num_followers = 10
leader_speed = 0.1
num_time_steps = 100
inertia = 0.0
force_function = force_random
#force_function = force_simple_comfortable_distance

df = run() #Generate the dataframe for plotting

output_notebook() #Tell bokeh to render things inside this notebook
show(bokeh_app) #Start the small bokeh plotting application

Loading BokehJS ...